Know Thy System
============================
Before we discuss the concepts of measurement errors and uncertainties we will first introduce the concept of calibration. We will

**Calibration** is an extremely important step in experiments as it allows us to confront our measurement system against a known **standard**.  The process of calibration allows us to understand the response of the measurement system (i.e. the output) to the input values and assert their relationship. 

### Standards 

The process of calibration relies on comparing the system's output to a reference value - *a standard*. 

**Primary Standards** are standards which are used for the defining the measurement unit - meter; second; Kg etc. Not all units are defined directly by primary standards, some, such as energy [J] or pressure [Pa] are derived from the base units. 

**Transfer standards** are calibrated based on primary standards and are then used to calibrate **local standards**, which in turn are used for calibrating **working** standards which are used for calibrating instruments. 

Not all laboratories will have a working standard. Many times, external organizations will calibrate the instruments periodically. 

Note however, that even when no *official* standards exist, a simple calibration or *sanity check* of the instrument is usually performed prior to the experiment itself.  These checks do not by any mean replace the need for formal periodic calibration, but they increase the user's confidence and serve to validate that unknown factors have not led to significant biases in the measurement. and


### A simple calibration example

In the [linked csv file](../BC/Temp.csv) you will find experimental data obtained from two different sources - a non-contact IR sensor which we wish to calibrate and a calibrated thermocouple (I have saved you the trouble and converted the thermocouple measurments to Kelvin). 


First we need to import some libraries :

In [1]:
import numpy as np 
import pandas as pd
import plotly.express as px
from scipy import optimize

Next, we use the pandas package to read in our csv file and reshape it. Note that the emphasize here is on making it easy to understand and not on proper usage of the python language.

In [2]:
df = pd.read_csv('Temp.csv')
df = df.drop(columns=df.columns[0])
df.head()

IR1        TC1       IR2        TC2       IR3        TC3       IR4  \
0  0.100000  33.966335  0.100000  33.980729  0.100000  34.082835  0.100000   
1  0.102634  35.116676  0.102634  32.230332  0.102634  34.818297  0.102634   
2  0.105268  30.092609  0.105268  36.143939  0.105268  33.194092  0.105268   
3  0.107903  33.151242  0.107903  34.130346  0.107903  33.057566  0.107903   
4  0.110537  34.467250  0.110537  36.130374  0.110537  28.626641  0.110537   

         TC4       IR5        TC5  
0  34.521812  0.100000  33.141800  
1  33.849606  0.102634  37.990984  
2  30.467709  0.105268  33.394834  
3  31.620905  0.107903  34.685687  
4  33.981638  0.110537  33.095601

In [3]:
IRdata = pd.melt(df, value_vars =['IR1','IR2','IR3','IR4','IR5'] )
Tdata = pd.melt(df, value_vars =['TC1','TC2','TC3','TC4','TC5'] )
fig = px.scatter(x=IRdata.value,y=Tdata.value,color = IRdata.variable, 
                 labels=dict(x="IR signal [V]", y="Temperature [K]", color="measurement"))
fig.show()

We will use Scipy's **optimize** function to obtain the calibration function. 
We will assume that the relation is given via a power law of the shape:
$$
T = a+b*V^c
$$

In [4]:
def IR2T(x,a,b,c):
    return(a+b*np.power(x,c))

In [5]:
fitted_params, cov = optimize.curve_fit(IR2T, IRdata.value, Tdata.value)   
stdevs = np.sqrt(np.diag(cov))
print(' a=' ,"%.2f" % fitted_params[0], u"\u00B1","%.3f" % stdevs[0],'\n',
      'b=' , "%.2f" % fitted_params[1],u"\u00B1","%.3f" % stdevs[1],'\n',
      'c =' , "%.2f" % fitted_params[2], u"\u00B1","%.3f" % stdevs[2])


 a= 25.06 ± 0.100 
 b= 44.13 ± 0.086 
 c = 0.76 ± 0.001


> Question: Try to see what happens by assuming a linear dependence between the voltage and temperature. For what range of temperatures do you think this calibration can be used?

As you observe, our calibration was done in the temperature range of 25 to 245 degrees leading to voltage variations of up to 8[V]. 
The range of validaty of future measurments is then set.  Any measurment outside this range is extraploated and we have no knowledge as to the behaviour of our system at those temperatures. 


As you noticed we used the concept of curve fitting for our calibration. Later we will dedicate some time to understand what is regression and how to interpert our results in a carefull way.